Determine the exceedance probability (WRA version) of water level of each site in each month. The calculation doesn't involve probability transformation so it's easier.

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

plt.style.use(['seaborn-colorblind', 'seaborn-talk'])
plt.rcParams['figure.dpi'] = 200
plt.rcParams['savefig.dpi'] = 200
plt.rcParams['savefig.bbox'] = 'tight'
plt.rcParams['font.sans-serif'] = ['Taipei Sans TC Beta'] # to plot Chinese words properly

import datetime
date = datetime.datetime.now().strftime('%Y%m%d')

# Read data

In [2]:
merge_df = pd.read_hdf('data/database_ZAF_clean_gps_20211107.hd5', key='wl')

In [6]:
merge_df.tail()

井名                 日期時間        井號  水面至井口深度         Lon  \
38292354  東石(4)  2021-09-21 23:10:00  10090141   17.349  120.154469   
38292355  東石(4)  2021-09-21 23:20:00  10090141   17.345  120.154469   
38292356  東石(4)  2021-09-21 23:30:00  10090141   17.342  120.154469   
38292357  東石(4)  2021-09-21 23:40:00  10090141   17.341  120.154469   
38292358  東石(4)  2021-09-21 23:50:00  10090141   17.342  120.154469   

                Lat  月  
38292354  23.460335  9  
38292355  23.460335  9  
38292356  23.460335  9  
38292357  23.460335  9  
38292358  23.460335  9

In [13]:
prob = 25
sample = merge_df.loc[(merge_df['井號'] == '10090141') & (merge_df['月'] == 9), '水面至井口深度'].values
sample.sort()
sample[int(prob/100*len(sample))]
#sample_std = np.std(sample)
#dist = stats.norm(loc=sample_mean, scale=sample_std)
#prob = [_*.01 for _ in range(0, 101)]
#values = [dist.ppf(_) for _ in prob]

15.860000000000001

In [12]:
merge_df.loc[(merge_df['井號'] == '10090141') & (merge_df['月'] == 9), '水面至井口深度'].values

array([17.4  , 17.32 , 17.23 , ..., 17.342, 17.341, 17.342])

## Multi-thread
Include slicing data (X) to the multi-threads, whcih enpwoers the multi-processing

In [14]:
from dask import delayed
from dask.distributed import Client
client = Client(memory_limit='25GB')

In [15]:
def get_cdf(merge_df, siteid, mon, probs):
    X = merge_df[(merge_df['井號'] == siteid) & (merge_df['月'] == mon)].copy()
    # only caculate when data amount is more than 4
    # to exclude the doubious excedance probability
    if len(X) > 4:
    # get the water levels of the selected probabilities
        sample = X['水面至井口深度'].values
        sample.sort()
        sample[int(prob/100*len(sample))]
        levels = [sample[int(prob/100*len(sample))] for prob in probs]
        # '井名', '井號', 'Lon', 'Lat', '月', 'levels'
        out = np.hstack([X.iloc[0, 0], X.iloc[0, 2], X.iloc[0, 4], 
                         X.iloc[0, 5], X.iloc[0, 6], levels])
    else:
        out = [None for _ in range(5+len(probs))]
    return out


def build_df(out_list, probs):
    return pd.DataFrame(out_list, columns=np.hstack(['井名', '井號', 'Lon', 'Lat', '月', probs]))


df_future = client.scatter(merge_df)
probs = [10, 20, 25, 35, 75, 85]
out_list = []

for siteid in merge_df['井號'].unique():
    for mon in range(1, 13):
        out_list.append(delayed(get_cdf)(df_future, siteid, mon, probs))
total = delayed(build_df)(out_list, probs)

In [16]:
total.visualize('results/build_prob_simple.svg')

In [17]:
%%time
lvl_df = total.compute()

Wall time: 41min 1s


In [18]:
clean_df = lvl_df[~lvl_df.Lon.isna()].copy()

In [19]:
print(lvl_df.shape)
print(clean_df.shape)

(3228, 11)
(2833, 11)


It is as same sa the output in `water_level_analysis_1.ipynb`.

In [21]:
clean_df.head()

井名    井號         Lon        Lat   月     10     20     25     35     75  \
0  二崙國小  4413  120.415102  23.771842   1  3.857  4.065   4.63   4.63  4.927   
3  二崙國小  4413  120.415102  23.771842   4  4.326   4.52   4.52   4.52  5.045   
4  二崙國小  4413  120.415102  23.771842   5  3.943  3.999  4.055  4.072   5.27   
7  二崙國小  4413  120.415102  23.771842   8    2.9  3.055  3.238  3.238  4.033   
9  二崙國小  4413  120.415102  23.771842  10  3.456  3.829  4.109  4.121  4.553   

      85  
0  4.927  
3  5.647  
4  5.339  
7  4.033  
9  4.887

In [20]:
clean_df.to_csv('data/wl_EP_simple_{}.csv'.format(date), index=False)
print(date)

20211117
